In [1]:
#import dependencies for plotting
import os
import numpy as np
import pandas as pd
from pathlib import Path
import matplotlib.pyplot as plt
import hvplot.pandas

# import dependencies for model
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error

In [2]:
#Load csv file

housing = ("Resources/Modified_housing.csv")

housing_df = pd.read_csv(housing)
housing_df

id     price  bedrooms  bathrooms  sqft_living  sqft_lot  \
0      7229300521  231300.0         2        1.0         1180      5650   
1      6414100192  538000.0         3        2.0         2570      7242   
2      5631500400  180000.0         2        1.0          770     10000   
3      2487200875  604000.0         4        3.0         1960      5000   
4      1954400510  510000.0         3        2.0         1680      8080   
...           ...       ...       ...        ...          ...       ...   
21605   263000018  360000.0         3        2.0         1530      1131   
21606  6600060120  400000.0         4        2.0         2310      5813   
21607  1523300141  402101.0         2        1.0         1020      1350   
21608   291310100  400000.0         3        2.0         1600      2388   
21609  1523300157  325000.0         2        1.0         1020      1076   

       floors  waterfront  view  yr_built  yr_renovated  zipcode      lat  \
0         1.0           0     0      1955             0    98178  47.5112   
1         2.0           0     0      1951          1991    98125  47.7210   
2         1.0           0     0      1933             0    98028  47.7379   
3         1.0           0     0      1965             0    98136  47.5208   
4         1.0           0     0      1987             0    98074  47.6168   
...       ...         ...   ...       ...           ...      ...      ...   
21605     3.0           0     0      2009             0    98103  47.6993   
21606     2.0           0     0      2014             0    98146  47.5107   
21607     2.0           0     0      2009             0    98144  47.5944   
21608     2.0           0     0      2004             0    98027  47.5345   
21609     2.0           0     0      2008             0    98144  47.5941   

          long    renovation_category  
0     -122.257        Never Renovated  
1     -122.319  Renovated before 2000  
2     -122.233        Never Renovated  
3     -122.393        Never Renovated  
4     -122.045        Never Renovated  
...        ...                    ...  
21605 -122.346        Never Renovated  
21606 -122.362        Never Renovated  
21607 -122.299        Never Renovated  
21608 -122.069        Never Renovated  
21609 -122.299        Never Renovated  

[21610 rows x 15 columns]

In [3]:
# Drop the original 'yr_renovated' column and ID
housing_df_cleaned = housing_df.drop(columns=['yr_renovated', 'id'])
housing_df_cleaned.head()

price  bedrooms  bathrooms  sqft_living  sqft_lot  floors  waterfront  \
0  231300.0         2        1.0         1180      5650     1.0           0   
1  538000.0         3        2.0         2570      7242     2.0           0   
2  180000.0         2        1.0          770     10000     1.0           0   
3  604000.0         4        3.0         1960      5000     1.0           0   
4  510000.0         3        2.0         1680      8080     1.0           0   

   view  yr_built  zipcode      lat     long    renovation_category  
0     0      1955    98178  47.5112 -122.257        Never Renovated  
1     0      1951    98125  47.7210 -122.319  Renovated before 2000  
2     0      1933    98028  47.7379 -122.233        Never Renovated  
3     0      1965    98136  47.5208 -122.393        Never Renovated  
4     0      1987    98074  47.6168 -122.045        Never Renovated

In [4]:
# Generate summary statistics
housing_df_cleaned.describe()

price      bedrooms     bathrooms   sqft_living      sqft_lot  \
count  2.161000e+04  21610.000000  21610.000000  21610.000000  2.161000e+04   
mean   5.400853e+05      3.370801      2.058723   2079.881212  1.510829e+04   
std    3.671522e+05      0.930153      0.755576    918.500299  4.142323e+04   
min    7.500000e+04      0.000000      0.000000    290.000000  5.200000e+02   
25%    3.216125e+05      3.000000      2.000000   1425.500000  5.040000e+03   
50%    4.500000e+05      3.000000      2.000000   1910.000000  7.619000e+03   
75%    6.450000e+05      4.000000      2.000000   2550.000000  1.068875e+04   
max    7.700000e+06     33.000000      8.000000  13540.000000  1.651359e+06   

             floors    waterfront          view      yr_built       zipcode  \
count  21610.000000  21610.000000  21610.000000  21610.000000  21610.000000   
mean       1.534891      0.007543      0.234197   1971.003609  98077.945673   
std        0.554753      0.086523      0.766136     29.372639     53.505373   
min        1.000000      0.000000      0.000000   1900.000000  98001.000000   
25%        1.000000      0.000000      0.000000   1951.000000  98033.000000   
50%        2.000000      0.000000      0.000000   1975.000000  98065.000000   
75%        2.000000      0.000000      0.000000   1997.000000  98118.000000   
max        4.000000      1.000000      4.000000   2015.000000  98199.000000   

                lat          long  
count  21610.000000  21610.000000  
mean      47.560049   -122.213910  
std        0.138572      0.140833  
min       47.155900   -122.519000  
25%       47.470925   -122.328000  
50%       47.571800   -122.231000  
75%       47.678000   -122.125000  
max       47.777600   -121.315000

In [5]:
# Plot your data to see what's in your DataFrame
housing_df_cleaned.hvplot.line(
    width=800,
    height=400,
    rot=90
)

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [6]:
# Encode the categorical column into dummy/indicator variables
dummies = pd.get_dummies(housing_df_cleaned, columns=['zipcode','renovation_category'], dtype=int)
dummies

price  bedrooms  bathrooms  sqft_living  sqft_lot  floors  \
0      231300.0         2        1.0         1180      5650     1.0   
1      538000.0         3        2.0         2570      7242     2.0   
2      180000.0         2        1.0          770     10000     1.0   
3      604000.0         4        3.0         1960      5000     1.0   
4      510000.0         3        2.0         1680      8080     1.0   
...         ...       ...        ...          ...       ...     ...   
21605  360000.0         3        2.0         1530      1131     3.0   
21606  400000.0         4        2.0         2310      5813     2.0   
21607  402101.0         2        1.0         1020      1350     2.0   
21608  400000.0         3        2.0         1600      2388     2.0   
21609  325000.0         2        1.0         1020      1076     2.0   

       waterfront  view  yr_built      lat  ...  zipcode_98168  zipcode_98177  \
0               0     0      1955  47.5112  ...              0              0   
1               0     0      1951  47.7210  ...              0              0   
2               0     0      1933  47.7379  ...              0              0   
3               0     0      1965  47.5208  ...              0              0   
4               0     0      1987  47.6168  ...              0              0   
...           ...   ...       ...      ...  ...            ...            ...   
21605           0     0      2009  47.6993  ...              0              0   
21606           0     0      2014  47.5107  ...              0              0   
21607           0     0      2009  47.5944  ...              0              0   
21608           0     0      2004  47.5345  ...              0              0   
21609           0     0      2008  47.5941  ...              0              0   

       zipcode_98178  zipcode_98188  zipcode_98198  zipcode_98199  \
0                  1              0              0              0   
1                  0              0              0              0   
2                  0              0              0              0   
3                  0              0              0              0   
4                  0              0              0              0   
...              ...            ...            ...            ...   
21605              0              0              0              0   
21606              0              0              0              0   
21607              0              0              0              0   
21608              0              0              0              0   
21609              0              0              0              0   

       renovation_category_Never Renovated  \
0                                        1   
1                                        0   
2                                        1   
3                                        1   
4                                        1   
...                                    ...   
21605                                    1   
21606                                    1   
21607                                    1   
21608                                    1   
21609                                    1   

       renovation_category_Renovated 2000-2010  \
0                                            0   
1                                            0   
2                                            0   
3                                            0   
4                                            0   
...                                        ...   
21605                                        0   
21606                                        0   
21607                                        0   
21608                                        0   
21609                                        0   

       renovation_category_Renovated 2010-2015  \
0                                            0   
1                                            0   
2                                            0   
3

In [7]:
# Selecting numerical features for standardization
numerical_features = ['price', 'bedrooms', 'bathrooms', 'sqft_living', 'sqft_lot', 'floors','lat', 'long']

# Standardizing the numerical features
scaler = StandardScaler()
dummies[numerical_features] = scaler.fit_transform(dummies[numerical_features])


In [8]:
kmeans = KMeans(n_clusters=3, random_state=42)  # Adjust number of clusters as needed
dummies['cluster'] = kmeans.fit_predict(dummies)

# Display the DataFrame with cluster assignments
display(dummies)


C:\Users\Juango\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1412: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


price  bedrooms  bathrooms  sqft_living  sqft_lot    floors  \
0     -0.841048 -1.473771  -1.401245    -0.979751 -0.228338 -0.964219   
1     -0.005680 -0.398654  -0.077721     0.533620 -0.189905  0.838426   
2     -0.980775 -1.473771  -1.401245    -1.426142 -0.123322 -0.964219   
3      0.174086  0.676463   1.245803    -0.130521 -0.244030 -0.964219   
4     -0.081944 -0.398654  -0.077721    -0.435373 -0.169674 -0.964219   
...         ...       ...        ...          ...       ...       ...   
21605 -0.490504 -0.398654  -0.077721    -0.598687 -0.337434  2.641071   
21606 -0.381555  0.676463  -0.077721     0.250543 -0.224403  0.838426   
21607 -0.375832 -1.473771  -1.401245    -1.153953 -0.332147  0.838426   
21608 -0.381555 -0.398654  -0.077721    -0.522474 -0.307088  0.838426   
21609 -0.585834 -1.473771  -1.401245    -1.153953 -0.338762  0.838426   

       waterfront  view  yr_built       lat  ...  zipcode_98177  \
0               0     0      1955 -0.352525  ...              0   
1               0     0      1951  1.161525  ...              0   
2               0     0      1933  1.283487  ...              0   
3               0     0      1965 -0.283245  ...              0   
4               0     0      1987  0.409552  ...              0   
...           ...   ...       ...       ...  ...            ...   
21605           0     0      2009  1.004924  ...              0   
21606           0     0      2014 -0.356133  ...              0   
21607           0     0      2009  0.247899  ...              0   
21608           0     0      2004 -0.184377  ...              0   
21609           0     0      2008  0.245734  ...              0   

       zipcode_98178  zipcode_98188  zipcode_98198  zipcode_98199  \
0                  1              0              0              0   
1                  0              0              0              0   
2                  0              0              0              0   
3                  0              0              0              0   
4                  0              0              0              0   
...              ...            ...            ...            ...   
21605              0              0              0              0   
21606              0              0              0              0   
21607              0              0              0              0   
21608              0              0              0              0   
21609              0              0              0              0   

       renovation_category_Never Renovated  \
0                                        1   
1                                        0   
2                                        1   
3                                        1   
4                                        1   
...                                    ...   
21605                                    1   
21606                                    1   
21607                                    1   
21608                                    1   
21609                                    1   

       renovation_category_Renovated 2000-2010  \
0                                            0   
1                                            0   
2                                            0   
3                                            0   
4                                            0   
...                                        ...   
21605                                        0   
21606                                        0   
21607                                        0   
21608                                        0   
21609                                        0   

       renovation_category_Renovated 2010-2015  \
0                                            0   
1                                            0   
2                                            0   
3                                            0   
4                                            0   
...                                        ..

In [10]:
# Split data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(dummies.drop(columns=['price']), dummies['price'], test_size=0.2, random_state=42)

# Initialize and train linear regression model
model = LinearRegression()
model.fit(X_train, y_train)

# Predict on test set
y_pred = model.predict(X_test)

# Evaluate model performance
mse = mean_squared_error(y_test, y_pred)
print(f"Mean Squared Error: {mse}")

Mean Squared Error: 0.22742620019080684


In [11]:
import numpy as np

# Compute the variance of the actual house prices
variance = np.var(y_test)

# Print the variance
print("Variance of House Prices:", variance)

# Calculate the ratio of MSE to variance
mse_to_variance_ratio = mse / variance

# Print the ratio
print("MSE to Variance Ratio:", mse_to_variance_ratio)

Variance of House Prices: 1.0503516242185489
MSE to Variance Ratio: 0.21652387157492106
